# Keyword speech recongnition

The idea is to use Convolution Neural Network to extract features of the framed specturm and classify the audio data.


## 1. Preprocessing

In [1]:
!pip install plotly
!pip install seaborn

    100% |████████████████████████████████| 24.9MB 49kB/s  eta 0:00:01
  Running setup.py bdist_wheel for plotly ... done
  Stored in directory: /root/.cache/pip/wheels/33/be/39/f82c0f53ea29777fdc29afaf7bfad87442488a280662d355fb
Successfully built plotly
You are using pip version 9.0.1, however version 10.0.1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.
    100% |████████████████████████████████| 184kB 4.2MB/s ta 0:00:01
  Running setup.py bdist_wheel for seaborn ... done
  Stored in directory: /root/.cache/pip/wheels/26/0a/44/53ddd89769e62f7c6691976375b86c6492e7dd20a2d3970e32
Successfully built seaborn
You are using pip version 9.0.1, however version 10.0.1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [2]:
%matplotlib inline
import os
import re
from glob import glob

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.plotly as py
import plotly.graph_objs as go
import numpy as np

from scipy.io import wavfile
import scipy
import numpy as np
import pandas as pd
from scipy import stats, integrate
import matplotlib.pyplot as plt
import seaborn as sns
sns.set(color_codes=True)
import IPython.display as ipd

import tensorflow as tf


from sklearn.model_selection import train_test_split
# from tensorflow.contrib.learn.python.learn.learn_io.generator_io import generator_input_fn

import keras
from keras.models import Sequential, load_model
from keras.layers import Dense, Dropout, Flatten
from keras.layers import Conv2D, MaxPooling2D, BatchNormalization

from keras.optimizers import Adam
from scipy import signal

import h5py

sns.set(style="whitegrid", color_codes=True)
init_notebook_mode(connected=True)

from keras.layers import Merge, Input, merge
from keras.layers.core import Dense, Dropout, Activation, Flatten, Reshape, Permute,Lambda, RepeatVector
from keras.layers.convolutional import ZeroPadding2D, AveragePooling2D, Conv2D,MaxPooling2D, Convolution1D,MaxPooling1D
from keras.layers.normalization import BatchNormalization
from keras.layers.merge import Multiply
from keras.layers import LSTM, SimpleRNN, GRU, TimeDistributed, Bidirectional
from keras import backend as K
from keras.models import Sequential,Model, load_model
import csv
from keras.utils.vis_utils import plot_model

Using TensorFlow backend.


In [3]:
DATA_PATH = '/audio_sample' # path to training data
TEMP_DATA_PATH = '/tmp/temp'
TRAIN_DATA_PATH = DATA_PATH + '/audio/'

VALIDATION_LIST_FILE_PATH = DATA_PATH + '/validation_list.txt'
TEST_LIST_FILE_PATH = DATA_PATH + '/testing_list.txt'
SAMPLE_FILES = glob(os.path.join(DATA_PATH, 'audio/*/*wav'))

In [4]:
os.listdir(DATA_PATH)

['.DS_Store',
 'audio',
 'validation_list.txt',
 'LICENSE',
 'testing_list.txt',
 'README.md']

In [5]:
folders = []
for file_folder in os.listdir(TRAIN_DATA_PATH):
    if os.path.isdir(TRAIN_DATA_PATH + file_folder):
        folders.append(file_folder)
print(folders)
print('There are totally ' + str(len(folders)) + ' labels in the training dataset.')

['five', 'seven', 'yes', 'on', 'marvin', 'six', 'off', 'two', 'happy', '_background_noise_', 'eight', 'dog', 'sheila', 'nine', 'bird', 'right', 'zero', 'four', 'cat', 'no', 'up', 'house', 'stop', 'go', 'wow', 'left', 'three', 'down', 'one', 'bed', 'tree']
There are totally 31 labels in the training dataset.


However, from the competition note, there are only 12 labels we have to pay attention to.
> **Note**: There are only 12 possible labels for the Test set: yes, no, up, down, left, right, on, off, stop, go, silence, unknown.

> The unknown label should be used for a command that is not one one of the first 10 labels or that is not silence.

In [6]:
POSSIBLE_LABELS = 'yes, no, up, down, left, right, on, off, stop, go, silence, unknown'.replace(' ', '').split(',')
print(POSSIBLE_LABELS)

['yes', 'no', 'up', 'down', 'left', 'right', 'on', 'off', 'stop', 'go', 'silence', 'unknown']


 The file *validation_list.txt* specifies the data for validation.

In [7]:
# validation files list
with open(VALIDATION_LIST_FILE_PATH, 'r') as file:
    valid_files_names = [line.rstrip() for line in file]

# test files list
with open(TEST_LIST_FILE_PATH, 'r') as file:
    test_files_names = [line.rstrip() for line in file]

In [8]:
sample_matcher = re.compile("(?:.+\/)?(\w+)\/([^_]+)_.+wav")
def get_info_from_path(path):
    """
        return (label, id)
    """
    r = sample_matcher.match(path)
    if not r:
        raise ValueError(path + ' is not valid file path')
    label = r.group(1)
    id = r.group(2)
    
    if label not in POSSIBLE_LABELS:
        if label == '_background_noise_':
            label = 'silence'
        else:
            label = 'unknown'
    return label, id

In [9]:
# extract info for validation and test files
valid_file_tuples = []
valid_id_set = {}
for file in valid_files_names:
    try: 
        label, id = get_info_from_path(file)
    except ValueError as e:
        print(e)
        continue
    valid_file_tuples.append((label, id, file))
    valid_id_set[id] = True

test_file_tuples = []
test_id_set = {}
for file in test_files_names:
    try: 
        label, id = get_info_from_path(file)
    except ValueError as e:
        print(e)
        continue
    test_file_tuples.append((label, id, file))
    test_id_set[id] = True

In [10]:
# train file is the file that neither in test or validation
file_path_matcher = re.compile("(.+\/)?(\w+\/[^_]+_.+wav)")
train_file_tuples = []

for file in SAMPLE_FILES:
    try:
        label, id = get_info_from_path(file)
    except ValueError as e:
        print(e)
        continue
    if (id not in valid_id_set) and (id not in test_id_set):
        train_file_tuples.append((label, id, file_path_matcher.match(file).group(2)))

In [11]:
print('Number of sample')
print('Total: %d' % len(SAMPLE_FILES))
print('Train: %d' % len(train_file_tuples))
print('Validation: %d' % len(valid_file_tuples))
print('Test: %d' % len(test_file_tuples))
number_sum = len(train_file_tuples) + len(valid_file_tuples) + len(test_file_tuples)
print('{} + {} + {} = {}'.format(len(train_file_tuples), len(valid_file_tuples), len(test_file_tuples), number_sum))

Number of sample
Total: 64727
Train: 51094
Validation: 6798
Test: 6835
51094 + 6798 + 6835 = 64727


### look at the data

#### a. distribution

In [12]:
# calculate the distribution of training and validation data
distribution = {}
for label, _, _ in train_file_tuples + valid_file_tuples:
    if label not in distribution:
        distribution[label] = 0
    distribution[label] = distribution[label] + 1

data = [go.Bar(
            x=[*distribution.keys()],
            y=[*distribution.values()]
    )]

iplot(data, filename='distribution')

When we look at the distribution of the data, **unknwon**, **silence** are two special labels. **unknown** has much more data than others, **silence** only has 6.


Ideas to handle the two special cases:
- train a model to seperate **silence** from the rest. Then we train another one to seperate **unknown** from the key words that we are interesting.

- bootstrap the other types

- throw away some of unknown words

In [13]:
distribution = {}
for label, _, _ in valid_file_tuples:
    if label not in distribution:
        distribution[label] = 0
    distribution[label] = distribution[label] + 1

data = [go.Bar(
            x=[*distribution.keys()],
            y=[*distribution.values()]
    )]

iplot(data, filename='distribution')

The wierd thing is that validation set does not have **silence**. So in order to train the silence detect model, I have to use the train set for both training and validation

#### b. audio length

In [14]:
sample_length_list = []

# read in every audio and count each length
for label, id, file in train_file_tuples + valid_file_tuples:
    sample_rate, samples = wavfile.read(TRAIN_DATA_PATH + file)
    sample_length_list.append(len(samples))

/usr/local/lib/python3.6/site-packages/scipy/io/wavfile.py:273: WavFileWarning:

Chunk (non-data) not understood, skipping it.



In [15]:
sample_rate = 16000
sample_length_list = np.array(sample_length_list)
sample_length_list[sample_length_list > sample_rate]

array([ 960000,  960000, 1522930,  978488,  988891,  980062])

In [16]:
train_valid_files = np.array(train_file_tuples + valid_file_tuples)
large_audio_files = train_valid_files[sample_length_list > sample_rate]
print(large_audio_files)

[['silence' 'white' '_background_noise_/white_noise.wav']
 ['silence' 'pink' '_background_noise_/pink_noise.wav']
 ['silence' 'doing' '_background_noise_/doing_the_dishes.wav']
 ['silence' 'running' '_background_noise_/running_tap.wav']
 ['silence' 'dude' '_background_noise_/dude_miaowing.wav']
 ['silence' 'exercise' '_background_noise_/exercise_bike.wav']]


There are some really long audio. Hopefully, there are not too much and they are those background noise. Let's hear some of them.

In [17]:
ipd.Audio(filename=TRAIN_DATA_PATH + large_audio_files[4][2])

**Some ideas to handle it:**
- chop the long file into 1 second length
- mix different types of noise
- mix noise with audio file

In [18]:
sample_rate = 16000
sample_length_list = np.array(sample_length_list)
sample_length_list[sample_length_list < 0.5 * sample_rate]

array([6688, 7431, 7431, 7431, 6688, 7431, 6688, 7431, 7431, 6827, 7431,
       7431, 5945, 7339, 7431, 7510, 6827, 7339, 7431, 7510, 6827, 7510,
       6688, 7431, 7851, 7510, 6144, 6827, 6827, 6827, 7510])

There are some very short audio. Also not too much.

In [19]:
truncated_sample_length = sample_length_list[sample_length_list <= 3 * sample_rate]
data = [go.Histogram(x=truncated_sample_length)]
iplot(data)

In [20]:
small_sample_num = len(sample_length_list[sample_length_list < sample_rate])
print('There are about %d samples smaller than the sample rate' % small_sample_num)

There are about 5865 samples smaller than the sample rate


**Some idea to handle short audio sample:**
- padding 0 to it
- stretch the audio to 1 seconds
- decompose it into phonome

**Load the data**

In [12]:
def pad_to_middle(sample, sample_rate=16000):
    pad_num = sample_rate - len(sample)
    left = int(pad_num / 2)
    right = pad_num - left
    return np.pad(sample, (left, right), 'constant')

In [13]:
def chop_data(sample, sample_rate=16000):
    """
        chop the data by cutting it into small pieces first
    """
    num = np.ceil(len(sample) / sample_rate).astype(np.int)
    pad_num = num * sample_rate - len(sample)
    return np.split(np.pad(sample, (0, pad_num), 'constant'), num)

In [14]:
def random_select(sample, sample_rate=16000):
    beg = np.random.randint(0, len(sample) - sample_rate)
    return sample[beg: beg + sample_rate]

In [15]:
def get_label(label):
    if label == 'silence':
        return 1
    return 0

**Load the training data**

In [16]:
train_data_list = []

# read file into memory
if len(train_data_list) < 1:
    for label, id, fname in train_file_tuples:
        sample_rate, sample = wavfile.read(TRAIN_DATA_PATH + fname)
        train_data_list.append((label, id, sample))

/usr/local/lib/python3.6/site-packages/scipy/io/wavfile.py:273: WavFileWarning:

Chunk (non-data) not understood, skipping it.



In [17]:
# extract the silence samples
silence_samples = list(filter(lambda t: t[0] == 'silence', train_data_list))
non_silence_samples = list(filter(lambda t: t[0] != 'silence', train_data_list))

In [18]:
# mkdir for sliced silence samples
SLICED_SILENCE_TRAIN_FILES_PATH = os.path.join(TEMP_DATA_PATH, 'augumented_data/short_silence_train')
SLICED_SILENCE_VALID_FILES_PATH = os.path.join(TEMP_DATA_PATH, 'augumented_data/short_silence_valid')

os.makedirs(SLICED_SILENCE_TRAIN_FILES_PATH, exist_ok=True)
os.makedirs(SLICED_SILENCE_VALID_FILES_PATH, exist_ok=True)

In [19]:
# output silence sample from 80% of the noise sample for trainning set
if True:
    for i in range(len(non_silence_samples)):
        index = np.random.randint(0, len(silence_samples))
        if len(silence_samples[index][2]) < 16000:
            print(silence_samples[index][1])
        
        end = int(len(silence_samples[index][2]) * 0.8)
        random_sample = random_select(silence_samples[index][2][:end], 16000)
        title = silence_samples[index][0]
        file_name = title + '_' + str(index) + '_' + str(i) + '.wav'
        wavfile.write(os.path.join(SLICED_SILENCE_TRAIN_FILES_PATH, file_name), 16000, random_sample)

In [20]:
# output silence sample from 20% of the noise sample for validation set
if True:
    for i in range(len(non_silence_samples)):
        index = np.random.randint(0, len(silence_samples))
        if len(silence_samples[index][2]) < 16000:
            print(silence_samples[i])
        beg = int(len(silence_samples[index][2]) * 0.8)
        random_sample = random_select(silence_samples[index][2][beg:], 16000)
        title = silence_samples[index][0]
        file_name = title + '_' + str(index) + '_' + str(i) + '.wav'
        wavfile.write(os.path.join(SLICED_SILENCE_VALID_FILES_PATH, file_name), 16000, random_sample)

In [21]:
# load the silence data for training 
silence_data_train =[]

for file in glob(os.path.join(SLICED_SILENCE_TRAIN_FILES_PATH, '*wav')):
    _, sample = wavfile.read(file)
    r = sample_matcher.match(file)
    silence_data_train.append(('silence', r.group(2), sample))
    
# load the silence data for validation

silence_data_valid =[]

for file in glob(os.path.join(SLICED_SILENCE_VALID_FILES_PATH, '*wav')):
    _, sample = wavfile.read(file)
    r = sample_matcher.match(file)
    silence_data_valid.append(('silence', r.group(2), sample))
    
# print count

print('Totally we have %d silence training data' % len(silence_data_train))
print('Totally we have %d silence valid data' % len(silence_data_valid))

Totally we have 51088 silence training data
Totally we have 51088 silence valid data


**Load validation data**

In [22]:
valid_data_list = []

if len(valid_data_list) < 1:
    for label, id, fname in valid_file_tuples:
        sample_rate, sample = wavfile.read(TRAIN_DATA_PATH + fname)
        valid_data_list.append((label, id, sample))

**Load the kaggle test data**

In [23]:
FINAL_TEST_FILE_PATH = '/audio_test/test/audio'
FINAL_TEST_FILES = glob(os.path.join(FINAL_TEST_FILE_PATH, '*wav'))

In [24]:
test_file_id_matcher = re.compile('_([^\.]+)')

In [25]:
test_samples_raw = []
for file_path in FINAL_TEST_FILES:
    uid = test_file_id_matcher.search(file_path).group(1)
    sample_rate, sample = wavfile.read(file_path)
    test_samples_raw.append((uid, sample))


## 2. CNN with spectrum
The idea is to chop the audio data into different frame. Take the frequency info from each frame and put those into CNN. As mentioned before, the plan is to build 3 models: detect silence, detect unkown, classify the data. And combine them finally.

**a. the first model is to detect the silence**

In [26]:
# there could be some more advanced way to mixup
silence_model_train_data = non_silence_samples + silence_data_train

# mixup can be used here
silence_model_valid_data = valid_data_list + silence_data_valid

**TF Estimator**

In [36]:
def silence_train_input_genetator(data_list=silence_model_train_data, sample_rate=16000):
    """
    To train the model to detect silence.
    For silence data we have to find some
    way to geneate some in order to handle
    the misbalance problem.
    """

    np.random.shuffle(silence_model_train_data)
    def generator():
        for label, id, sample in data_list:
            try:
                sample = sample.astype(np.float32) / np.iinfo(np.int16).max
                if len(sample) < sample_rate:
                    samples = [pad_to_middle(sample)]
                elif len(sample) > sample_rate:
                    samples = chop_data(sample)
                else:
                    samples = [sample]
                for one_second_sample in samples:
                    yield dict(
                        target=np.int32(get_label(label)),
                        wav=one_second_sample
                    )
            except Exception as err:
                print(err, label, id, fname)

    
    return generator

In [ ]:
def silence_eval_input_genetator(data_list=silence_model_valid_data, sample_rate=16000):
    """
    To train the model to detect silence.
    For silence data we have to find some
    way to geneate some in order to handle
    the misbalance problem.
    """
    def generator():
        for label, id, sample in data_list:
            try:
                sample = sample.astype(np.float32) / np.iinfo(np.int16).max
                if len(sample) < sample_rate:
                    samples = [pad_to_middle(sample)]
                elif len(sample) > sample_rate:
                    samples = [chop_data(sample)[0]]
                else:
                    samples = [sample]
                for one_second_sample in samples:
                    yield dict(
                        target=np.int32(get_label(label)),
                        wav=one_second_sample
                    )
            except Exception as err:
                print(err, label, id, fname)

    
    return generator

In [ ]:
from tensorflow.contrib import layers, signal
def silence_model_handler(features, labels, mode, params, config):
    
    ### ================ Define the CNN ==========================
    sample = features['wav']
    is_training = mode == tf.estimator.ModeKeys.TRAIN
    x = tf.abs(signal.stft(sample, 400, 160))
    x = tf.stack([x], axis=3)
    x = tf.to_float(x)
    x = layers.batch_norm(x, is_training=is_training)
    for i in range(3):
        x = layers.conv2d(
            x, 8 * (2 ** i), 3, 1,
            normalizer_fn=layers.batch_norm,
            normalizer_params={'is_training': is_training}
        )
        x = layers.max_pool2d(x, 2, 2)
    x = layers.flatten(x)
    x = tf.layers.dense(x, 128, activation=tf.nn.relu)
    x = layers.dropout(x, keep_prob=params['keep_prob'] if is_training else 1.0)
    x = tf.layers.dense(x, 64, activation=tf.nn.relu)
    logits = tf.layers.dense(x, 2, activation=None)

    ### ===========================================================
    
    if mode == tf.estimator.ModeKeys.TRAIN:
        loss = tf.reduce_mean(
            tf.nn.sparse_softmax_cross_entropy_with_logits(labels=labels, logits=logits))
        train_op=layers.optimize_loss(
            loss=loss,
            global_step=tf.train.get_global_step(),
            learning_rate=0.001,
            optimizer=tf.train.AdamOptimizer
        )
        
        specs = {'mode': mode, 'loss': loss, 'train_op': train_op}
    
    if mode == tf.estimator.ModeKeys.EVAL:
        prediction = tf.argmax(logits, axis=-1)
        acc, acc_op = tf.metrics.mean_per_class_accuracy(
            labels, prediction, 2)
        loss = tf.reduce_mean(
            tf.nn.sparse_softmax_cross_entropy_with_logits(labels=labels, logits=logits))
        specs = dict(
                mode=mode,
                loss=loss,
                eval_metric_ops=dict(
                    acc=(acc, acc_op),
                )
        )
    
    if mode == tf.estimator.ModeKeys.PREDICT:
        predictions = {
            'label': tf.argmax(logits, axis=-1),  
            'sample': features['wav'], 
        }
        specs = {
            'mode': mode,
            'predictions': predictions,
        }
    return tf.estimator.EstimatorSpec(**specs)

In [ ]:
OUT_PATH = os.path.join('./', 'out')
os.makedirs(OUT_PATH, exist_ok=True)
params = {
    'keep_prob': True
}
run_config = tf.contrib.learn.RunConfig(
    model_dir=OUT_PATH, 
    log_step_count_steps=10,
    save_summary_steps=10
)
silence_model = tf.estimator.Estimator(
    model_fn=silence_model_handler, params=params, config=run_config)

In [ ]:
# silence_model_input_fn = silence_train_input_from_memory(silence_model_train_data)
silence_model_input_fn = generator_input_fn(
    x=silence_train_input_genetator(silence_model_train_data),
    target_key='target',
    shuffle=True,
    num_epochs=None,
    batch_size=50,
    queue_capacity=3 * 50 + 10, num_threads=1,
)


In [ ]:
# train_input = lambda: silence_train_input_from_memory(data_list)
silence_model.train(input_fn=silence_model_input_fn, steps=300)

In [ ]:
silence_model_eval_input_fn = generator_input_fn(
    x=silence_eval_input_genetator(silence_model_valid_data),
    target_key='target'
)

In [ ]:
silence_model.evaluate(input_fn=silence_model_eval_input_fn)

The Estimator from tensorflow is not very developer friendly, hard to learn and also need a lot of redundancy codes. So I switch to keras which is very friendly

**Keras**

In [36]:
def log_specgram(audio, sample_rate=16000, window_size=20,
                 step_size=10, eps=1e-10):
    nperseg = int(round(window_size * sample_rate / 1e3))
    noverlap = int(round(step_size * sample_rate / 1e3))
    freqs, times, spec = scipy.signal.spectrogram(audio,
                                    fs=sample_rate,
                                    window='hann',
                                    nperseg=nperseg,
                                    noverlap=noverlap,
                                    detrend=False)
    return np.log(spec.T.astype(np.float32) + eps)

In [34]:
def shuffle_onehot_spectrum_transform_silence(samples):
    np.random.shuffle(samples)
    
    x = list(map(lambda t: t[2], samples))
    y = list(map(lambda t: 1 if t[0] == 'silence' else 0, samples))
    y = keras.utils.to_categorical(y, num_classes=2)
    
    x = list(map(pad_to_middle, x))
    spectrum = np.stack(map(log_specgram, x))
    spectrum = np.array(spectrum)
    spectrum = spectrum.reshape(-1, 99, 161, 1)
    
    return spectrum, y

In [39]:
silence_model_train_data_x_spectrum, silence_model_train_data_y = shuffle_onehot_spectrum_transform_silence(silence_model_train_data)


KeyboardInterrupt: 

In [ ]:
silence_model_valid_data_x_spectrum, silence_model_valid_data_y = shuffle_onehot_spectrum_transform_silence(silence_model_valid_data)


silence_model_h5py = h5py.File('silence_model_data')
silence_model_h5py.create_dataset('silence_model_train_data_x_spectrum', data=silence_model_train_data_x_spectrum)
silence_model_h5py.create_dataset('silence_model_train_data_y', data=silence_model_train_data_y)
silence_model_h5py.create_dataset('silence_model_valid_data_x_spectrum', data=silence_model_valid_data_x_spectrum)
silence_model_h5py.create_dataset('silence_model_valid_data_y', data=silence_model_valid_data_y)
silence_model_h5py.close()

In [41]:
silence_model_h5py = h5py.File('silence_model_data', 'r')
silence_model_train_data_x_spectrum = silence_model_h5py['silence_model_train_data_x_spectrum']
silence_model_train_data_y = silence_model_h5py['silence_model_train_data_y']
silence_model_valid_data_x_spectrum = silence_model_h5py['silence_model_valid_data_x_spectrum']
silence_model_valid_data_y = silence_model_h5py['silence_model_valid_data_y']

**Vgg model 1**

In [41]:
def vgg_layers_1(model):
    model.add(BatchNormalization(input_shape=(99, 161,1)))
    model.add(Conv2D(32, (3, 3), activation='relu'))
    model.add(Conv2D(32, (3, 3), activation='relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(BatchNormalization())

    model.add(Conv2D(64, (3, 3), activation='relu'))
    model.add(Conv2D(64, (3, 3), activation='relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(BatchNormalization())

    model.add(Conv2D(256, (3, 3), activation='relu'))
    model.add(Conv2D(256, (3, 3), activation='relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(BatchNormalization())

    model.add(Conv2D(512, (3, 3), activation='relu'))
    model.add(Conv2D(512, (3, 3), activation='relu'))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(BatchNormalization())
    model.add(Dropout(0.25))

    model.add(Flatten())
    model.add(Dense(256, activation='relu'))
    model.add(Dropout(0.5))
    model.add(Dense(128, activation='relu'))
    model.add(Dropout(0.5))

silence_model = Sequential()
vgg_layers_1(silence_model)
silence_model.add(Dense(2, activation='softmax'))

adam = Adam(lr=1e-5)
silence_model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['acc'])

In [44]:
checkpoint = keras.callbacks.ModelCheckpoint(
    filepath=os.path.join('./', 'silence-checkpoint-{epoch:02d}-{acc:.2f}.hdf5'))

In [47]:
silence_model.fit(x=silence_model_train_data_x_spectrum, y=silence_model_train_data_y, 
                  batch_size=32, epochs=5, callbacks=[checkpoint],
                  validation_data=(silence_model_valid_data_x_spectrum, silence_model_valid_data_y),
                  shuffle="batch"
                 )

Train on 102176 samples, validate on 57886 samples
Epoch 1/5
102176/102176 [==============================] - 141s - loss: 0.1297 - acc: 0.9517 - val_loss: 0.0861 - val_acc: 0.9636
Epoch 2/5
102176/102176 [==============================] - 116s - loss: 0.0333 - acc: 0.9890 - val_loss: 0.0205 - val_acc: 0.9940
Epoch 3/5
102176/102176 [==============================] - 116s - loss: 0.0134 - acc: 0.9960 - val_loss: 0.0679 - val_acc: 0.9756
Epoch 4/5
102176/102176 [==============================] - 116s - loss: 0.0043 - acc: 0.9987 - val_loss: 0.0086 - val_acc: 0.9970
Epoch 5/5
102176/102176 [==============================] - 116s - loss: 0.0018 - acc: 0.9994 - val_loss: 1.1643e-04 - val_acc: 1.0000


In [48]:
silence_model.save('silence_model')

The vgg model above is not suitable for audio recongnition (it is designed for computer vision). So I also tried the following conv net from [google tensorflow speech command](https://github.com/tensorflow/tensorflow/blob/master/tensorflow/examples/speech_commands/models.py).

**vgg model 2 from google speech command**

In [48]:
def vgg_google(model):
    model.add(BatchNormalization(input_shape=(99, 161,1)))
    model.add(Conv2D(64, (8, 20), activation='relu'))
    model.add(Dropout(0.25))
    model.add(MaxPooling2D(pool_size=(2, 2)))

    model.add(Conv2D(64, (4, 10), activation='relu', padding='same'))
    model.add(Dropout(0.25))

    model.add(Flatten())

    
silence_model_google = Sequential()
vgg_google(silence_model_google)
silence_model_google.add(Dense(2, activation='softmax'))

adam = Adam(lr=1e-5)
silence_model_google.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['acc'])

In [51]:
checkpoint = keras.callbacks.ModelCheckpoint(
    filepath=os.path.join('./', 'silence-google-checkpoint-{epoch:02d}-{acc:.2f}.hdf5'))
silence_model_google.fit(x=silence_model_train_data_x_spectrum, y=silence_model_train_data_y, 
                  batch_size=32, epochs=5, callbacks=[checkpoint],shuffle="batch",
                  validation_data=(silence_model_valid_data_x_spectrum, silence_model_valid_data_y)
)

Train on 102176 samples, validate on 57886 samples
Epoch 1/5
102176/102176 [==============================] - 98s - loss: 0.0251 - acc: 0.9916 - val_loss: 0.0041 - val_acc: 0.9999
Epoch 2/5
102176/102176 [==============================] - 97s - loss: 0.0023 - acc: 0.9995 - val_loss: 0.0038 - val_acc: 1.0000
Epoch 3/5
102176/102176 [==============================] - 97s - loss: 9.4421e-04 - acc: 0.9998 - val_loss: 0.0042 - val_acc: 1.0000
Epoch 4/5
102176/102176 [==============================] - 97s - loss: 0.0014 - acc: 0.9997 - val_loss: 0.0073 - val_acc: 0.9995
Epoch 5/5
102176/102176 [==============================] - 96s - loss: 3.0615e-04 - acc: 0.9999 - val_loss: 0.0014 - val_acc: 1.0000


In [52]:
silence_model_google.save('silence_model_google')

The result is very high. But consider the validation, training set comes from the same source. The model may overfitting.

**mixed silence with samples model**

Mix up the silence and audio
(label, 0.8 * audio + 0.1 * noise1 + 0.1 * noise2) vs (silence, noise)

In [27]:
def mixup(audio, noises):
    noise_index_1 = np.random.randint(len(noises))
    noise_index_2 = np.random.randint(len(noises))
    if len(audio) < 16000:
        audio = pad_to_middle(audio)
    mixed_audio = 0.8 * audio + 0.1 * random_select(noises[noise_index_1]) + 0.1 * random_select(noises[noise_index_2])
    return mixed_audio

In [28]:
MIXUP_SILENCE_TRAIN_PATH = os.path.join(TEMP_DATA_PATH ,'augumented_data/mixup_silence_train')
MIXUP_SILENCE_VALID_PATH = os.path.join(TEMP_DATA_PATH, 'augumented_data/mixup_silence_valid')

os.makedirs(MIXUP_SILENCE_TRAIN_PATH, exist_ok=True)
os.makedirs(MIXUP_SILENCE_VALID_PATH, exist_ok=True)

silence_train_samples = list(map(lambda t: t[2][:int(0.8 * len(t[2]))], silence_samples))
silence_valid_samples = list(map(lambda t: t[2][int(0.8 * len(t[2])):], silence_samples))


if True:
    for _ in range(int(0.3 * len(non_silence_samples))):
        index = np.random.randint(len(non_silence_samples))
        label, uid, sample = non_silence_samples[index]
        mixed_sample = mixup(sample, silence_train_samples)
        file_name = 'label' + '_mixed_' + str(index) + '_' + str(uid) + '.wav'
        wavfile.write(os.path.join(MIXUP_SILENCE_TRAIN_PATH, file_name), 16000, mixed_sample)

if True:
    for _ in range(int(0.3 * len(valid_data_list))):
        index = np.random.randint(len(valid_data_list))
        label, uid, sample = valid_data_list[index]
        mixed_sample = mixup(sample, silence_train_samples)
        file_name = 'label' + '_mixed_' + str(index) + '_' + str(uid) + '.wav'
        wavfile.write(os.path.join(MIXUP_SILENCE_VALID_PATH, file_name), 16000, mixed_sample)

In [29]:
def load_path(path):
    files = glob(os.path.join(path, '*.wav'))
    samples = []
    for file in files:
        sample_rate, sample = wavfile.read(file)
        label, id = get_info_from_path(file)
        samples.append((label, id, sample))
    return samples

In [30]:
mixed_train_samples_no_silence = load_path(MIXUP_SILENCE_TRAIN_PATH)
mixed_valid_samples_no_silence = load_path(MIXUP_SILENCE_VALID_PATH)
np.random.shuffle(mixed_train_samples_no_silence)
np.random.shuffle(mixed_valid_samples_no_silence)
print('Mixed silence train number %d' % len(mixed_train_samples_no_silence))
print('Mixed silence valid number %d' % len(mixed_valid_samples_no_silence))

Mixed silence train number 13185
Mixed silence valid number 1759


In [31]:
np.random.shuffle(silence_data_train)
np.random.shuffle(silence_data_valid)


mixed_train_samples = mixed_train_samples_no_silence + \
                        silence_data_train[:len(mixed_train_samples_no_silence)] + \
                        non_silence_samples
mixed_valid_samples = mixed_valid_samples_no_silence + \
                        silence_data_valid[:len(mixed_valid_samples_no_silence)] + \
                        valid_data_list

In [37]:
mixed_train_x_spectrum, mixed_train_data_y = shuffle_onehot_spectrum_transform_silence(mixed_train_samples)

In [38]:
mixed_valid_data_x_spectrum, mixed_valid_data_y = shuffle_onehot_spectrum_transform_silence(mixed_valid_samples)

In [39]:
mixed_silence_data = h5py.File('mixed_silence_data')
mixed_silence_data.create_dataset('train_x_spectrum', data=mixed_train_x_spectrum)
mixed_silence_data.create_dataset('train_y', data=mixed_train_data_y)
mixed_silence_data.create_dataset('valid_x_spectrum', data=mixed_valid_data_x_spectrum)
mixed_silence_data.create_dataset('valid_y', data=mixed_valid_data_y)
mixed_silence_data.close()

RuntimeError: Unable to create link (name already exists)

In [ ]:
mixed_silence_data = h5py.File('mixed_silence_data', 'r')
mixed_train_x_spectrum = mixed_silence_data['mixed_silence_data']
mixed_train_data_y = mixed_silence_data['mixed_train_data_y']
mixed_train_x_spectrum = mixed_silence_data['mixed_train_x_spectrum']
mixed_valid_data_y = mixed_silence_data['mixed_valid_data_y']

In [42]:
mixed_silence_model = Sequential()
vgg_layers_1(mixed_silence_model)
mixed_silence_model.add(Dense(2, activation='softmax'))

adam = Adam(lr=1e-5)
mixed_silence_model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['acc'])

In [43]:
checkpoint = keras.callbacks.ModelCheckpoint(
    filepath=os.path.join('./', 'mixed-silence-checkpoint-{epoch:02d}-{acc:.2f}.hdf5'))

In [53]:
mixed_silence_model.fit(x=mixed_train_x_spectrum, y=mixed_train_data_y, 
                  batch_size=32, epochs=5, callbacks=[checkpoint],
                  validation_data=(mixed_valid_data_x_spectrum, mixed_valid_data_y)
)

Train on 77458 samples, validate on 10316 samples
Epoch 1/5
77458/77458 [==============================] - 75s - loss: 0.0100 - acc: 0.9967 - val_loss: 0.0954 - val_acc: 0.9785
Epoch 2/5
77458/77458 [==============================] - 75s - loss: 0.0074 - acc: 0.9978 - val_loss: 0.0304 - val_acc: 0.9869
Epoch 3/5
77458/77458 [==============================] - 75s - loss: 0.0059 - acc: 0.9984 - val_loss: 0.1280 - val_acc: 0.9770
Epoch 4/5
77458/77458 [==============================] - 75s - loss: 0.0059 - acc: 0.9981 - val_loss: 0.0252 - val_acc: 0.9880
Epoch 5/5
77458/77458 [==============================] - 75s - loss: 0.0033 - acc: 0.9991 - val_loss: 0.1582 - val_acc: 0.9771


In [46]:
mixed_silence_model.save('mixed_silence_model')

**google speech**

In [49]:
mixed_silence_google_model = Sequential()
vgg_google(mixed_silence_google_model)
mixed_silence_google_model.add(Dense(2, activation='softmax'))

adam = Adam(lr=1e-5)
mixed_silence_google_model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['acc'])

In [50]:
checkpoint = keras.callbacks.ModelCheckpoint(
    filepath=os.path.join('./', 'mixed-silence-google-checkpoint-{epoch:02d}-{acc:.2f}.hdf5'))

In [55]:
mixed_silence_google_model.fit(x=mixed_train_x_spectrum, y=mixed_train_data_y, 
                  batch_size=32, epochs=5, callbacks=[checkpoint],
                  validation_data=(mixed_valid_data_x_spectrum, mixed_valid_data_y)
)

Train on 77458 samples, validate on 10316 samples
Epoch 1/5
77458/77458 [==============================] - 62s - loss: 0.0078 - acc: 0.9977 - val_loss: 0.1720 - val_acc: 0.9741
Epoch 2/5
77458/77458 [==============================] - 62s - loss: 0.0055 - acc: 0.9986 - val_loss: 0.1343 - val_acc: 0.9783
Epoch 3/5
77458/77458 [==============================] - 62s - loss: 0.0060 - acc: 0.9984 - val_loss: 0.1522 - val_acc: 0.9752
Epoch 4/5
77458/77458 [==============================] - 62s - loss: 0.0045 - acc: 0.9988 - val_loss: 0.1445 - val_acc: 0.9747
Epoch 5/5
77458/77458 [==============================] - 62s - loss: 0.0055 - acc: 0.9985 - val_loss: 0.1768 - val_acc: 0.9732


In [52]:
mixed_silence_google_model.save('mixed_silence_google_model')


** b. the second model is to detect unknown words**

For this model, validation set has enough classess for use.

In [95]:
# set a class label for the data, 1: unknown, 0: others 
class_dict = {}
for label, uid, sample in non_silence_samples:
    if label not in class_dict:
        class_dict[label] = 1 if label == 'unknown' else 0
print(class_dict)

{'no': 0, 'unknown': 1, 'yes': 0, 'off': 0, 'right': 0, 'on': 0, 'go': 0, 'down': 0, 'left': 0, 'up': 0, 'stop': 0}


In [96]:
def shuffle_onehot_spectrum_transform(samples, class_dict=class_dict):
    np.random.shuffle(samples)
    
    x = list(map(lambda t: t[2], samples))
    y = list(map(lambda t: class_dict[t[0]], samples))
    y = keras.utils.to_categorical(y, num_classes=len(class_dict))
    
    x = list(map(pad_to_middle, x))
    spectrum = np.stack(map(log_specgram, x))
    spectrum = np.array(spectrum)
    spectrum = spectrum.reshape(-1, 99, 161, 1)
    
    return spectrum, y

In [97]:
train_x_spectrum, train_y_one_hot = shuffle_onehot_spectrum_transform(non_silence_samples)

NameError: name 'log_specgram' is not defined

In [ ]:
valid_x_spectrum, valid_y_one_hot = shuffle_onehot_spectrum_transform(valid_data_list)

In [ ]:
unknown_model = Sequential()
vgg_layers_1(unknown_model)
unknown_model.add(Dense(2, activation='softmax'))

adam = Adam(lr=1e-5)
unknown_model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['acc'])


In [ ]:
checkpoint = keras.callbacks.ModelCheckpoint(filepath=os.path.join('out', 'checkpoint-unknown-{epoch:02d}-{val_loss:.2f}.hdf5'))
unknown_model.fit(train_x_spectrum, train_y_one_hot, validation_data=(valid_x_spectrum, valid_y_one_hot), 
          batch_size=32, epochs=30, callbacks=[checkpoint])

In [ ]:
if False:
    unknown_model.save('./unknown_model')

**google vgg**

In [ ]:
unknown_model_google = Sequential()
vgg_layers_1(unknown_model_google)
unknown_model_google.add(Dense(2, activation='softmax'))

adam = Adam(lr=1e-5)
unknown_model_google.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['acc'])


In [ ]:
checkpoint = keras.callbacks.ModelCheckpoint(filepath=os.path.join('out', 'checkpoint-unknown_model_google-{epoch:02d}-{val_loss:.2f}.hdf5'))
unknown_model_google.fit(train_x_spectrum, train_y_one_hot, validation_data=(valid_x_spectrum, valid_y_one_hot), 
          batch_size=32, epochs=30, callbacks=[checkpoint])

In [ ]:
if False:
    unknown_model_google.save('./unknown_model_google')

**b-2. classify all non-silence data together**

In [99]:
class_dict = {}
for label, uid, sample in non_silence_samples:
    if label not in class_dict:
        class_dict[label] = len(class_dict)
print(class_dict)

{'stop': 0, 'unknown': 1, 'up': 2, 'off': 3, 'no': 4, 'go': 5, 'yes': 6, 'on': 7, 'right': 8, 'down': 9, 'left': 10}


In [100]:
class_dict = {'unknown': 0, 'right': 1, 'off': 2, 'left': 3, 'on': 4, 'yes': 5, 'up': 6, 'go': 7, 'no': 8, 'down': 9, 'stop': 10}

In [101]:
train_x_spectrum, train_y_one_hot = shuffle_onehot_spectrum_transform(non_silence_samples, class_dict)

In [102]:
valid_x_spectrum, valid_y_one_hot = shuffle_onehot_spectrum_transform(valid_data_list, class_dict)

**vgg**

In [64]:
classes_model = Sequential()
vgg_layers_1(classes_model)
classes_model.add(Dense(11, activation='softmax'))

adam = Adam(lr=1e-4)
classes_model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['acc'])


In [69]:
checkpoint = keras.callbacks.ModelCheckpoint(filepath=os.path.join(TEMP_DATA_PATH, 'classes-model-checkpoint-unknown-{epoch:02d}-{val_loss:.2f}.hdf5'))
classes_model.fit(train_x_spectrum, train_y_one_hot, validation_data=(valid_x_spectrum, valid_y_one_hot), 
          batch_size=32, epochs=5, callbacks=[checkpoint])

Train on 51088 samples, validate on 6798 samples
Epoch 1/5
51088/51088 [==============================] - 50s - loss: 0.4227 - acc: 0.8686 - val_loss: 0.3126 - val_acc: 0.9113
Epoch 2/5
51088/51088 [==============================] - 50s - loss: 0.3057 - acc: 0.9087 - val_loss: 0.2851 - val_acc: 0.9134
Epoch 3/5
51088/51088 [==============================] - 50s - loss: 0.2427 - acc: 0.9303 - val_loss: 0.2441 - val_acc: 0.9329
Epoch 4/5
51088/51088 [==============================] - 50s - loss: 0.2050 - acc: 0.9415 - val_loss: 0.2301 - val_acc: 0.9347
Epoch 5/5
51088/51088 [==============================] - 50s - loss: 0.1709 - acc: 0.9516 - val_loss: 0.2258 - val_acc: 0.9432


In [70]:
classes_model.save('classes_model')

**google**

In [71]:
classes_model_google = Sequential()
vgg_google(classes_model_google)
classes_model_google.add(Dense(11, activation='softmax'))

adam = Adam(lr=1e-5)
classes_model_google.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['acc'])

In [73]:
checkpoint = keras.callbacks.ModelCheckpoint(filepath=os.path.join(TEMP_DATA_PATH, 'classes_silence_model_google-checkpoint-unknown-{epoch:02d}-{val_loss:.2f}.hdf5'))
classes_model_google.fit(train_x_spectrum, train_y_one_hot, validation_data=(valid_x_spectrum, valid_y_one_hot), 
          batch_size=32, epochs=3, callbacks=[checkpoint])

Train on 51088 samples, validate on 6798 samples
Epoch 1/3
51088/51088 [==============================] - 42s - loss: 0.6003 - acc: 0.8124 - val_loss: 0.6942 - val_acc: 0.7885
Epoch 2/3
51088/51088 [==============================] - 42s - loss: 0.5310 - acc: 0.8333 - val_loss: 0.6299 - val_acc: 0.8029
Epoch 3/3
51088/51088 [==============================] - 42s - loss: 0.4780 - acc: 0.8504 - val_loss: 0.5888 - val_acc: 0.8248


In [76]:
classes_model_google.save('classes_model_google')

**rnn**

In [44]:
n_time = 99
n_freq = 161
num_classes = 11

def block(input):
    cnn = Conv2D(128, (3, 3), padding="same", activation="linear", use_bias=False)(input)
    cnn = BatchNormalization(axis=-1)(cnn)

    cnn1 = Lambda(slice1, output_shape=slice1_output_shape)(cnn)
    cnn2 = Lambda(slice2, output_shape=slice2_output_shape)(cnn)

    cnn1 = Activation('linear')(cnn1)
    cnn2 = Activation('sigmoid')(cnn2)

    out = Multiply()([cnn1, cnn2])
    return out

def slice1(x):
    return x[:, :, :, 0:64]

def slice2(x):
    return x[:, :, :, 64:128]

def slice1_output_shape(input_shape):
    return tuple([input_shape[0],input_shape[1],input_shape[2],64])

def slice2_output_shape(input_shape):
    return tuple([input_shape[0],input_shape[1],input_shape[2],64])

# Attention weighted sum
def outfunc(vects):
    cla, att = vects    # (N, n_time, n_out), (N, n_time, n_out)
    att = K.clip(att, 1e-7, 1.)
    out = K.sum(cla * att, axis=1) / K.sum(att, axis=1)     # (N, n_out)
    return out

def rnn(model,num_classes):
    a1 = Reshape((n_time, n_freq, 1))(model) # (N, 99, 161, 1)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 81, 128)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 41, 128)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 21, 128)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 11, 128)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 5, 128)
    
    a1 = Conv2D(256, (3, 3), padding="same", activation="relu", use_bias=True)(a1)
    a1 = MaxPooling2D(pool_size=(1, 5))(a1) # (N, 99, 1, 256)
    
    a1 = Reshape((99, 256))(a1) # (N, 99, 256)
    
    # Gated BGRU
    rnnout = Bidirectional(GRU(128, activation='linear', return_sequences=True))(a1)
    rnnout_gate = Bidirectional(GRU(128, activation='sigmoid', return_sequences=True))(a1)
    a2 = Multiply()([rnnout, rnnout_gate])
    
    # Attention
    cla = TimeDistributed(Dense(num_classes, activation='sigmoid'), name='localization_layer')(a2)
    att = TimeDistributed(Dense(num_classes, activation='softmax'))(a2)
    out = Lambda(outfunc, output_shape=(num_classes,))([cla, att])
    return Model(input_logmel, out)

input_logmel = Input(shape=(n_time, n_freq, 1), name='in_layer')   # (N, 99, 161)
rnn_model = rnn(input_logmel, num_classes)
rnn_model.compile(loss='binary_crossentropy',
                  optimizer='adam',
                  metrics=['accuracy'])

In [ ]:
checkpoint = keras.callbacks.ModelCheckpoint(filepath=os.path.join(TEMP_DATA_PATH, 'rnn_model-checkpoint-unknown-{epoch:02d}-{val_loss:.2f}.hdf5'))
rnn_model.fit(train_x_spectrum, train_y_one_hot, validation_data=(valid_x_spectrum, valid_y_one_hot), 
          batch_size=32, epochs=3, callbacks=[checkpoint])

Train on 51088 samples, validate on 6798 samples
Epoch 1/3
51088/51088 [==============================] - 878s - loss: 0.1045 - acc: 0.9629 - val_loss: 0.0598 - val_acc: 0.9784
Epoch 2/3
51088/51088 [==============================] - 881s - loss: 0.0394 - acc: 0.9862 - val_loss: 0.0563 - val_acc: 0.9809
Epoch 3/3
39168/51088 [======================>.......] - ETA: 199s - loss: 0.0296 - acc: 0.9901

In [90]:
rnn_model.save('rnn_model')

In [91]:
test_data = []

for label, uid, path in test_file_tuples:
    sample_rate, sample = wavfile.read(os.path.join(DATA_PATH, 'audio', path))
    test_data.append((label, uid, sample))

In [92]:
test_x_spectrum, test_y = shuffle_onehot_spectrum_transform(test_data, class_dict)

In [93]:
rnn_model.evaluate(x=test_x_spectrum, y=test_y)

6835/6835 [==============================] - 24s    


[0.032526497917976051, 0.9889605747493585]

** get Kaggle test score **

In [85]:
test_file_id_matcher = re.compile('_([^\.]+)')

In [68]:
uids = np.array([test_file_id_matcher.search(item[0]).group(1) for item in test_samples_raw])

In [40]:
def test_spectrum_transform(samples):
    x = list(map(lambda t: t[1], samples))
    x = list(map(pad_to_middle, x))
    spectrum = np.stack(map(log_specgram, x))
    spectrum = np.array(spectrum)
    spectrum = spectrum.reshape(-1, 99, 161, 1)
    
    return spectrum

In [41]:
test_spectrum = test_spectrum_transform(test_samples_raw)

In [18]:
silence_model = load_model('silence_model')

In [21]:
plot_model(silence_model, to_file='silence_model.png', show_shapes=True, show_layer_names=True)

In [24]:
silence_result = silence_model.predict(test_spectrum, verbose=1)
print(len(silence_result))
silence_result_index = [np.argmax(t) for t in silence_result]
print(sum(silence_result_index))

158538/158538 [==============================] - 63s    
158538
13339


In [27]:
silence_result_index_h5py = h5py.File('silence_result_index')
silence_result_index_h5py.create_dataset('silence_result_index', data=silence_result_index)
silence_result_index_h5py.close()

In [22]:
silence_model_google = load_model('silence_model_google')

In [26]:
silence_model_google_result = silence_model_google.predict(test_spectrum, verbose=1)
print(len(silence_model_google_result))
silence_model_google_result_index = [np.argmax(t) for t in silence_model_google_result]
print(sum(silence_model_google_result_index))

158538/158538 [==============================] - 35s    
158538
27004


In [29]:
silence_result_google_index_h5py = h5py.File('silence_result_google_index')
silence_result_google_index_h5py.create_dataset('silence_result_google_index', data=silence_model_google_result_index)
silence_result_google_index_h5py.close()

In [ ]:
uids_h5f = h5py.File('temp/uids.h5', 'w')
uids_h5f.create_dataset('uids', data=uids)
uids_h5f.close()

In [24]:
classes_model = load_model('classes_model')

In [25]:
plot_model(classes_model, to_file='classes_model.png', show_shapes=True, show_layer_names=True)

In [34]:
classes_model_result = classes_model.predict(test_spectrum, verbose=1)
print(len(classes_model_result))
classes_model_result_index = [np.argmax(t) for t in classes_model_result]

158432/158538 [============================>.] - ETA: 0s158538
306617


In [29]:
classes_model_google = load_model('classes_model_google')

In [39]:
classes_model_google_result = classes_model_google.predict(test_spectrum, verbose=1)
print(len(classes_model_google_result))
classes_model_google_result_index = [np.argmax(t) for t in classes_model_google_result]

158400/158538 [============================>.] - ETA: 0s158538
269672


In [27]:
rnn_model = load_model('rnn_model')


In [28]:
plot_model(rnn_model, to_file='rnn_model.png', show_shapes=True, show_layer_names=True)

In [ ]:
rnn_model_result = rnn_model.predict(test_spectrum, verbose=1)
print(len(rnn_model_result))
rnn_model_result_index = [np.argmax(t) for t in rnn_model_result]

 48672/158538 [========>.....................] - ETA: 378s

In [70]:
class_dict = {'unknown': 0, 'right': 1, 'off': 2, 'left': 3, 'on': 4, 'yes': 5, 'up': 6, 'go': 7, 'no': 8, 'down': 9, 'stop': 10}

In [78]:
model_results_file = h5py.File('model_results')
model_results_file.create_dataset('silence_result_index', data=silence_result_index)
model_results_file.create_dataset('silence_model_google_result_index', data=silence_model_google_result_index)
model_results_file.create_dataset('classes_model_result_index', data=classes_model_result_index)
model_results_file.create_dataset('classes_model_google_result_index', data=classes_model_google_result_index)
model_results_file.create_dataset('rnn_model_result_index', data=rnn_model_result_index)
model_results_file.create_dataset('classes', data=classes)
model_results_file.close()

In [71]:
class_reverse_dict = {}
for key, value in class_dict.items():
    class_reverse_dict[value] = key

In [82]:
uids[:10]

array(['test/test/audio/clip_f7e7fec28', 'test/test/audio/clip_b272f8069',
       'test/test/audio/clip_f38f0cdf4', 'test/test/audio/clip_cb0518bef',
       'test/test/audio/clip_32487c681', 'test/test/audio/clip_42481e7bd',
       'test/test/audio/clip_5804d9b47', 'test/test/audio/clip_188737fa6',
       'test/test/audio/clip_f5ae9915d', 'test/test/audio/clip_1bdcf422c'],
      dtype='<U30')

In [93]:
len(result_index)

NameError: name 'result_index' is not defined

In [99]:
classes_silence_result = []

for uid, index, silence_index in zip(uids, classes_model_result_index, silence_result_index):
    if silence_index == 1:
        classes_silence_result.append((uid, 'silence'))
    else:
        classes_silence_result.append((uid, class_reverse_dict[index]))

In [101]:
with open('classes_silence_result.csv', 'w', newline='') as csvfile:
    fieldnames = ['fname', 'label']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for uid, label in classes_silence_result:
         writer.writerow({'fname': 'clip_' + uid + '.wav', 'label': label})

In [102]:
classes_silence_google_result = []

for uid, index, silence_index in zip(uids, classes_model_result_index, silence_model_google_result_index):
    if silence_index == 1:
        classes_silence_google_result.append((uid, 'silence'))
    else:
        classes_silence_google_result.append((uid, class_reverse_dict[index]))

In [103]:
with open('classes_silence_google_result.csv', 'w', newline='') as csvfile:
    fieldnames = ['fname', 'label']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for uid, label in classes_silence_google_result:
         writer.writerow({'fname': 'clip_' + uid + '.wav', 'label': label})

In [105]:
classes_google_silence_result = []

for uid, index, silence_index in zip(uids, classes_model_google_result_index, silence_result_index):
    if silence_index == 1:
        classes_google_silence_result.append((uid, 'silence'))
    else:
        classes_google_silence_result.append((uid, class_reverse_dict[index]))

In [106]:
with open('classes_google_silence_result.csv', 'w', newline='') as csvfile:
    fieldnames = ['fname', 'label']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for uid, label in classes_google_silence_result:
         writer.writerow({'fname': 'clip_' + uid + '.wav', 'label': label})

In [107]:
classes_google_silence_google_result = []

for uid, index, silence_index in zip(uids, classes_model_google_result_index, silence_model_google_result_index):
    if silence_index == 1:
        classes_google_silence_google_result.append((uid, 'silence'))
    else:
        classes_google_silence_google_result.append((uid, class_reverse_dict[index]))

In [108]:
with open('classes_google_silence_google_result.csv', 'w', newline='') as csvfile:
    fieldnames = ['fname', 'label']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for uid, label in classes_google_silence_google_result:
         writer.writerow({'fname': 'clip_' + uid + '.wav', 'label': label})

In [109]:
classes_rnn_silence_result = []

for uid, index, silence_index in zip(uids, rnn_model_result_index, silence_result_index):
    if silence_index == 1:
        classes_rnn_silence_result.append((uid, 'silence'))
    else:
        classes_rnn_silence_result.append((uid, class_reverse_dict[index]))

In [110]:
with open('classes_rnn_silence_result.csv', 'w', newline='') as csvfile:
    fieldnames = ['fname', 'label']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for uid, label in classes_rnn_silence_result:
         writer.writerow({'fname': 'clip_' + uid + '.wav', 'label': label})

In [112]:
classes_rnn_silence_google_result = []

for uid, index, silence_index in zip(uids, rnn_model_result_index, silence_model_google_result_index):
    if silence_index == 1:
        classes_rnn_silence_google_result.append((uid, 'silence'))
    else:
        classes_rnn_silence_google_result.append((uid, class_reverse_dict[index]))

In [113]:
with open('classes_rnn_silence_google_result.csv', 'w', newline='') as csvfile:
    fieldnames = ['fname', 'label']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for uid, label in classes_rnn_silence_google_result:
         writer.writerow({'fname': 'clip_' + uid + '.wav', 'label': label})

|    private, public   |  vgg_classes  | google_vgg_classess |  rnn_classes  |
|----------------------|:-------------:|:-------------------:|:-------------:|
|  **vgg_silence**     |0.78632,0.77850|   0.59250,0.58305   |0.76142,0.74314|
|**vgg_silence_google**|0.78292,0.77521|   0.59109,0.58141   |0.75883,0.74067|


#### Compare model parameters


In [32]:
params = {
    'silence': silence_model.count_params(),
    'silence_google': silence_model_google.count_params(),
    'class_vgg': classes_model.count_params(),
    'google_class_vgg': classes_model_google.count_params(),
    'rnn_class': rnn_model.count_params(),
}

In [40]:
for key, value in params.items():
    print('%s: %d' % (key, value))

silence: 5952486
silence_google: 592262
class_vgg: 5953647
google_class_vgg: 2473487
rnn_class: 1414550


#### rnn before cnn

In [52]:
n_time = 99
n_freq = 161
num_classes = 11

def rnn_vgg(model,num_classes):
    
    rnnout = Bidirectional(GRU(128, activation='linear', return_sequences=True))(model)
    rnnout_gate = Bidirectional(GRU(128, activation='sigmoid', return_sequences=True))(model)
    a2 = Multiply()([rnnout, rnnout_gate])
    
    a1 = Reshape((n_time, n_freq, 128))(a2) # (N, 99, 161, 1)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 81, 128)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 41, 128)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 21, 128)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 11, 128)
    
    a1 = block(a1)
    a1 = block(a1)
    a1 = MaxPooling2D(pool_size=(1, 2))(a1) # (N, 99, 5, 128)
    
    a1 = Conv2D(256, (3, 3), padding="same", activation="relu", use_bias=True)(a1)
    a1 = MaxPooling2D(pool_size=(1, 5))(a1) # (N, 99, 1, 256)
    
    a1 = Reshape((99, 256))(a1) # (N, 99, 256)
    
    # Gated BGRU
    
    
    # Attention
    cla = TimeDistributed(Dense(num_classes, activation='sigmoid'), name='localization_layer')(a1)
    att = TimeDistributed(Dense(num_classes, activation='softmax'))(a1)
    out = Lambda(outfunc, output_shape=(num_classes,))([cla, att])
    return Model(input_logmel, out)

input_logmel = Input(shape=(n_time, n_freq, 1), name='in_layer')   # (N, 99, 161)
rnn_vgg_model = rnn(input_logmel, num_classes)
rnn_vgg_model.compile(loss='binary_crossentropy',
                  optimizer='adam',
                  metrics=['accuracy'])

In [ ]:
checkpoint = keras.callbacks.ModelCheckpoint(filepath=os.path.join(TEMP_DATA_PATH, 'rnn_vgg_model-checkpoint-unknown-{epoch:02d}-{val_loss:.2f}.hdf5'))
rnn_vgg_model.fit(train_x_spectrum, train_y_one_hot, validation_data=(valid_x_spectrum, valid_y_one_hot), 
          batch_size=32, epochs=3, callbacks=[checkpoint])

Train on 51088 samples, validate on 6798 samples
Epoch 1/3
51088/51088 [==============================] - 921s - loss: 0.1276 - acc: 0.9549 - val_loss: 0.0712 - val_acc: 0.9730
Epoch 2/3
51088/51088 [==============================] - 855s - loss: 0.0807 - acc: 0.9705 - val_loss: 0.0964 - val_acc: 0.9634
Epoch 3/3
50848/51088 [============================>.] - ETA: 3s - loss: 0.0604 - acc: 0.9778

In [ ]:
rnn_vgg_model.save('rnn_vgg_model')

In [29]:
rnn_vgg_model = load_model('rnn_vgg_model')

In [31]:
plot_model(rnn_vgg_model, to_file='rnn_vgg_model.png', show_shapes=True, show_layer_names=True)

In [48]:
rnn_vgg_model_result = rnn_vgg_model.predict(test_spectrum, verbose=1)
print(len(rnn_vgg_model_result))
rnn_vgg_model_result_index = [np.argmax(t) for t in rnn_vgg_model_result]

158538/158538 [==============================] - 526s   
158538


In [51]:
model_results_file = h5py.File('model_results')
model_results_file.create_dataset('rnn_vgg_model_result_index', data=rnn_vgg_model_result_index)
model_results_file.close()

In [52]:
model_results_file = h5py.File('model_results')

In [60]:
rnn_vgg_model_result_index = model_results_file['rnn_vgg_model_result_index']

In [64]:
silence_result_index = model_results_file['silence_result_index']

In [72]:
classes_vgg_rnn_silence_result = []

for uid, index, silence_index in zip(uids, rnn_vgg_model_result_index, silence_result_index):
    if silence_index == 1:
        classes_vgg_rnn_silence_result.append((uid, 'silence'))
    else:
        classes_vgg_rnn_silence_result.append((uid, class_reverse_dict[index]))

In [76]:
with open('classes_vgg_rnn_silence_result.csv', 'w', newline='') as csvfile:
    fieldnames = ['fname', 'label']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for uid, label in classes_vgg_rnn_silence_result:
         writer.writerow({'fname': 'clip_' + uid + '.wav', 'label': label})